### <center>San Jose State University<br>Department of Applied Data Science<br><br>**DATA 200<br>Computational Programming for Data Analytics**<br><br>Spring 2024<br>Instructor: Ron Mak</center>

# Plot earthquake data with the `pandas` module

In [ ]:
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd

%matplotlib inline

In [ ]:
quakes = pd.read_csv('earthquakes.csv')
quakes.head()

## Cumulative distribution function (CDF)

#### Suppose that we want to know the probability of a value of interest being less than or equal to a particular value. This is the **cumulative disribution function (CDF)**. Using the `statsmodels` package, we can estimate the CDF giving us the **empirical cumulative distribution function (ECDF)**:

In [ ]:
from statsmodels.distributions.empirical_distribution import ECDF

ecdf = ECDF(quakes.query('magType == "ml"').mag)
plt.plot(ecdf.x, ecdf.y)

plt.xlabel('mag')
plt.ylabel('cumulative probability')
plt.title('ECDF of earthquake magnitude with magType ml')

plt.show()

#### For example, can make it clear that the probability of getting an earthquake with magnitude less than or equal to 3  using the `ml` scale is 98%:

In [ ]:
from statsmodels.distributions.empirical_distribution import ECDF

ecdf = ECDF(quakes.query('magType == "ml"').mag)
plt.plot(ecdf.x, ecdf.y)

plt.xlabel('mag')
plt.ylabel('cumulative probability')

# Add reference lines for interpreting the ECDF for mag <= 3.
plt.plot(
    [3, 3], [0, .98], '--k', 
    [-1.5, 3], [0.98, 0.98], '--k', alpha=0.4
)

# Set axis ranges.
plt.ylim(0, None)
plt.xlim(-1.25, None)

plt.title('P(mag <= 3) = 98%')
plt.show()

## `DataFrame groupby()`method
#### The `groupby()` method collect identical data into groups and perform aggregate functions on the grouped data. See [Pandas groupby() Explained With Examples](https://sparkbyexamples.com/pandas/pandas-groupby-explained-with-examples/)
#### For example:

In [ ]:
technologies = (
    {
        'Courses':  ["Spark" ,"PySpark", "Hadoop", "Python",
                     "Pandas", "Hadoop", "Spark", "Python", "NA"],
        'Fee':      [22000, 25000, 23000, 24000, 
                     26000, 25000, 25000, 22000, 1500],
        'Duration': ['30 days', '50 days', '55 days', '40 days',
                     '60 days', '35 days', '30 days', '50 days',
                     '40 days'],
        'Discount': [1000, 2300, 1000, 1200, 
                     2500, None, 1400, 1600, 0]
    }
)

df = pd.DataFrame(technologies)
df

#### The `sum()` method calculates the sum of each group:

In [ ]:
df_1 = df.groupby(['Courses']).sum()
df_1

#### We can group by multiple columns: 

In [ ]:
df_2 = df.groupby(['Courses', 'Duration']).sum()
df_2

## Box plots

#### Use `groupby()` to see the distribution of magnitudes across the different measurement methods for earthquakes by making a box plot of each group:

In [ ]:
quakes[['mag', 'magType']].groupby('magType').boxplot(
    figsize=(15, 8), subplots=False
)

plt.title('Earthquake Magnitude Box Plots by magType')
plt.ylabel('magnitude')

## Bar charts

#### Dataframe method `value_counts()` returns a `Series` object containing counts in descending order.

In [ ]:
quakes.parsed_place.value_counts()

#### Pass keyword argument `kind=bar` for vertical bars and `kind=barh` for horizontal bars.

In [ ]:
quakes.magType.value_counts().plot(
    kind='bar', 
    title='Earthquakes Recorded per magType', 
    rot=0
)

plt.xlabel('magType')
plt.ylabel('earthquakes')

plt.show()

### Plot the top 15 values.

In [ ]:
quakes.parsed_place.value_counts().iloc[14]

In [ ]:
quakes.parsed_place.value_counts().iloc[14::-1]

In [ ]:
quakes.parsed_place.value_counts().iloc[14::-1,].plot(
    kind='barh', figsize=(10, 8),
    title='Top 15 Places for Earthquakes '
          '(September 18, 2018 - October 13, 2018)'
)

plt.xlabel('earthquakes')
plt.show()

In [ ]:
quakes.groupby('parsed_place').tsunami.sum() \
    .sort_values()

In [ ]:
quakes.groupby('parsed_place').tsunami.sum() \
    .sort_values().iloc[-10:]

In [ ]:
quakes.groupby('parsed_place').tsunami.sum() \
    .sort_values().iloc[-10:].plot(
        kind='barh', figsize=(10,6), 
        title='Top 10 Places for Tsunamis '
              '(September 18, 2018 - October 13, 2018)'
)

plt.xlabel('tsunamis')
plt.show()

## Lambda function

#### A ***lambda function*** is an unnamed function that is applied to each element of a series. For example, the lambda function below converts each time value, represented by parameter `x`.
#### To display all the rows of a dataframe:

In [ ]:
pd.set_option('display.max_rows', None)

In [ ]:
quakes.query('parsed_place == "Indonesia"') \
    .assign(
        time=lambda x: pd.to_datetime(x.time, unit='ms'),
        earthquake=1
    )

## More bar charts

#### The `resample()` function for time series data rearranges the data by a different time unit (daily in the example below) for frequency calculations.

In [ ]:
indonesia_quakes = quakes.query('parsed_place == "Indonesia"') \
    .assign(
        time=lambda x: pd.to_datetime(x.time, unit='ms'),
        earthquake=1
    ).set_index('time').resample('1D').sum()

#### Format the datetimes in the index for the x-axis.

In [ ]:
indonesia_quakes.index = indonesia_quakes.index.strftime('%b\n%d')
indonesia_quakes.index

#### Plot the number of earthquakes and tsunamis together, day by day.

In [ ]:
indonesia_quakes.plot(
    y=['earthquake', 'tsunami'], kind='bar', figsize=(15, 7), 
    rot=0, label=['earthquakes', 'tsunamis'], 
    title='Earthquakes and Tsunamis in Indonesia '
          '(September 18, 2018 - October 13, 2018)'
)

plt.xlabel('date')
plt.ylabel('count')

plt.show()

## Stacked bars

In [ ]:
pivoted_table = quakes.assign(
    mag_bin=lambda x: np.floor(x.mag)
).pivot_table(
    index='mag_bin', columns='magType', 
    values='mag', aggfunc='count'
)

pivoted_table.plot.bar(
    stacked=True, rot=0, ylabel='earthquakes', 
    title='Earthquakes by integer magnitude and magType'
)

plt.show()

In [ ]:
normalized_pivoted_table = pivoted_table.fillna(0) \
    .apply(lambda x: x/x.sum(), axis=1)

ax = normalized_pivoted_table.plot.bar(
    stacked=True, rot=0, figsize=(10, 5),
    title='Percentage of earthquakes by integer magnitude for each magType'
)

# Move legend to the right of the plot.
ax.legend(bbox_to_anchor=(1, 0.8)) 
plt.ylabel('percentage')

plt.show()

In [ ]:
plt.close()

#### Adapted from ***Hands-On Data Analysis with Pandas, second edition***, by Stephanie Molin, Packt 2021, ISBN 978-1-80056-345-2

In [ ]:
# Additional material (c) 2024 by Ronald Mak